- analyze a Google Merchandise Store (also known as GStore, where Google swag is sold) customer dataset to predict revenue per customer. 
- we're predicting the natural log of the total revenue per unique user

In [2]:
from keras.models import Sequential
from keras.layers import Dense
from keras.wrappers.scikit_learn import KerasRegressor
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import KFold
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline

In [3]:
from pyspark.sql.types import *
from pyspark.sql.functions import *
from pyspark.ml import Pipeline
from pyspark.ml.regression import RandomForestRegressor
from pyspark.ml.feature import VectorIndexer
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml.feature import OneHotEncoderEstimator, StringIndexer, VectorAssembler
import pandas as pd
import numpy as np
import json

In [4]:
# File location and type
file_location = "/FileStore/tables/train.csv"
file_type = "csv"

# CSV options
infer_schema = "false"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
train = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .option('quote', '"') \
  .option('escape', '"') \
  .load(file_location)

display(train)

channelGrouping date device fullVisitorId geoNetwork sessionId socialEngagementType totals trafficSource visitId visitNumber visitStartTime Organic Search 20160902 {"browser": "Chrome", "browserVersion": "not available in demo dataset", "browserSize": "not available in demo dataset", "operatingSystem": "Windows", "operatingSystemVersion": "not available in demo dataset", "isMobile": false, "mobileDeviceBranding": "not available in demo dataset", "mobileDeviceModel": "not available in demo dataset", "mobileInputSelector": "not available in demo dataset", "mobileDeviceInfo": "not available in demo dataset", "mobileDeviceMarketingName": "not available in demo dataset", "flashVersion": "not available in demo dataset", "language": "not available in demo dataset", "screenColors": "not available in demo dataset", "screenResolution": "not available in demo dataset", "deviceCategory": "desktop"} 1131660440785968503 {"continent": "Asia", "subContinent": "Western Asia", "country": "Turkey", "region": "Izmir", "metro": "(not set)", "city": "Izmir", "cityId": "not available in demo dataset", "networkDomain": "ttnet.com.tr", "latitude": "not available in demo dataset", "longitude": "not available in demo dataset", "networkLocation": "not available in demo dataset"} 1131660440785968503_1472830385 Not Socially Engaged {"visits": "1", "hits": "1", "pageviews": "1", "bounces": "1", "newVisits": "1"} {"campaign": "(not set)", "source": "google", "medium": "organic", "keyword": "(not provided)", "adwordsClickInfo": {"criteriaParameters": "not available in demo dataset"}} 1472830385 1 1472830385 Organic Search 20160902 {"browser": "Firefox", "browserVersion": "not available in demo dataset", "browserSize": "not available in demo dataset", "operatingSystem": "Macintosh", "operatingSystemVersion": "not available in demo dataset", "isMobile": false, "mobileDeviceBranding": "not available in demo dataset", "mobileDeviceModel": "not available in demo dataset", "mobileInputSelector": "not available in demo dataset", "mobileDeviceInfo": "not available in demo dataset", "mobileDeviceMarketingName": "not available in demo dataset", "flashVersion": "not available in demo dataset", "language": "not available in demo dataset", "screenColors": "not available in demo dataset", "screenResolution": "not available in demo dataset", "deviceCategory": "desktop"} 377306020877927890 {"continent": "Oceania", "subContinent": "Australasia", "country": "Australia", "region": "not available in demo dataset", "metro": "not available in demo dataset", "city": "not available in demo dataset", "cityId": "not available in demo dataset", "networkDomain": "dodo.net.au", "latitude": "not available in demo dataset", "longitude": "not available in demo dataset", "networkLocation": "not available in demo dataset"} 377306020877927890_1472880147 Not Socially Engaged {"visits": "1", "hits": "1", "pageviews": "1", "bounces": "1", "newVisits": "1"} {"campaign": "(not set)", "source": "google", "medium": "organic", "keyword": "(not provided)", "adwordsClickInfo": {"criteriaParameters": "not available in demo dataset"}} 1472880147 1 1472880147 Organic Search 20160902 {"browser": "Chrome", "browserVersion": "not available in demo dataset", "browserSize": "not available in demo dataset", "operatingSystem": "Windows", "operatingSystemVersion": "not available in demo dataset", "isMobile": false, "mobileDeviceBranding": "not available in demo dataset", "mobileDeviceModel": "not available in demo dataset", "mobileInputSelector": "not available in demo dataset", "mobileDeviceInfo": "not available in demo dataset", "mobileDeviceMarketingName": "not available in demo dataset", "flashVersion": "not available in demo dataset", "language": "not available in demo dataset", "screenColors": "not available in demo dataset", "screenResolution": "not available in demo dataset", "deviceCategory": "desktop"} 3895546263509774583 {"continent": "Europe", "subContinent": "Southern Europe", "country": "Spain", "reg

In [5]:
# get the length of all json columns 
def udf_calculate_json_len(col):
  j_col = json.loads(col)
  return len(j_col)
udf_calculate_json_len = udf(udf_calculate_json_len, IntegerType())



display(
  train.select('device', udf_calculate_json_len('device').alias('len')).sort(desc('len'))
)

device len {"browser": "Chrome", "browserVersion": "not available in demo dataset", "browserSize": "not available in demo dataset", "operatingSystem": "Windows", "operatingSystemVersion": "not available in demo dataset", "isMobile": false, "mobileDeviceBranding": "not available in demo dataset", "mobileDeviceModel": "not available in demo dataset", "mobileInputSelector": "not available in demo dataset", "mobileDeviceInfo": "not available in demo dataset", "mobileDeviceMarketingName": "not available in demo dataset", "flashVersion": "not available in demo dataset", "language": "not available in demo dataset", "screenColors": "not available in demo dataset", "screenResolution": "not available in demo dataset", "deviceCategory": "desktop"} 16 {"browser": "Firefox", "browserVersion": "not available in demo dataset", "browserSize": "not available in demo dataset", "operatingSystem": "Macintosh", "operatingSystemVersion": "not available in demo dataset", "isMobile": false, "mobileDeviceBranding": "not available in demo dataset", "mobileDeviceModel": "not available in demo dataset", "mobileInputSelector": "not available in demo dataset", "mobileDeviceInfo": "not available in demo dataset", "mobileDeviceMarketingName": "not available in demo dataset", "flashVersion": "not available in demo dataset", "language": "not available in demo dataset", "screenColors": "not available in demo dataset", "screenResolution": "not available in demo dataset", "deviceCategory": "desktop"} 16 {"browser": "Chrome", "browserVersion": "not available in demo dataset", "browserSize": "not available in demo dataset", "operatingSystem": "Windows", "operatingSystemVersion": "not available in demo dataset", "isMobile": false, "mobileDeviceBranding": "not available in demo dataset", "mobileDeviceModel": "not available in demo dataset", "mobileInputSelector": "not available in demo dataset", "mobileDeviceInfo": "not available in demo dataset", "mobileDeviceMarketingName": "not available in demo dataset", "flashVersion": "not available in demo dataset", "language": "not available in demo dataset", "screenColors": "not available in demo dataset", "screenResolution": "not available in demo dataset", "deviceCategory": "desktop"} 16 {"browser": "UC Browser", "browserVersion": "not available in demo dataset", "browserSize": "not available in demo dataset", "operatingSystem": "Linux", "operatingSystemVersion": "not available in demo dataset", "isMobile": false, "mobileDeviceBranding": "not available in demo dataset", "mobileDeviceModel": "not available in demo dataset", "mobileInputSelector": "not available in demo dataset", "mobileDeviceInfo": "not available in demo dataset", "mobileDeviceMarketingName": "not available in demo dataset", "flashVersion": "not available in demo dataset", "language": "not available in demo dataset", "screenColors": "not available in demo dataset", "screenResolution": "not available in demo dataset", "deviceCategory": "desktop"} 16 {"browser": "Chrome", "browserVersion": "not available in demo dataset", "browserSize": "not available in demo dataset", "operatingSystem": "Android", "operatingSystemVersion": "not available in demo dataset", "isMobile": true, "mobileDeviceBranding": "not available in demo dataset", "mobileDeviceModel": "not available in demo dataset", "mobileInputSelector": "not available in demo dataset", "mobileDeviceInfo": "not available in demo dataset", "mobileDeviceMarketingName": "not available in demo dataset", "flashVersion": "not available in demo dataset", "language": "not available in demo dataset", "screenColors": "not available in demo dataset", "screenResolution": "not available in demo dataset", "deviceCategory": "mobile"} 16 {"browser": "Chrome", "browserVersion": "not available in demo dataset", "browserSize": "not available in demo dataset", "operatingSystem": "Windows", "operatingSystemVersion": "not available in demo dataset", "isMobile": false, "mobileDeviceBranding": "not available in demo dataset", "mobi

In [6]:

geoNetworkSchema = StructType(
  [
    StructField("continent", StringType()),
    StructField("subContinent", StringType()),
    StructField("country", StringType()),
    StructField("region", StringType()),
    StructField("metro", StringType()),
    StructField("city", StringType()),
    StructField("cityId", StringType()),
    StructField("networkDomain", StringType()),
    StructField("latitude", StringType()),
    StructField("longitude", StringType()),
    StructField("networkLocation", StringType()),
  ]
)


deviceSchema = StructType(
  [
    StructField("browser", StringType()),
    StructField("browserVersion", StringType()),
    StructField("browserSize", StringType()),
    StructField("operatingSystem", StringType()),
    StructField("operatingSystemVersion", StringType()),
    StructField("isMobile", StringType()),
    StructField("mobileDeviceBranding", StringType()),
    StructField("mobileDeviceModel", StringType()),
    StructField("mobileInputSelector", StringType()),
    StructField("mobileDeviceInfo", StringType()),
    StructField("mobileDeviceMarketingName", StringType()),
    StructField("flashVersion", StringType()),
    StructField("language", StringType()),
    StructField("screenColors", StringType()),
    StructField("screenResolution", StringType()),
    StructField("deviceCategory", StringType()),
  ]
)

In [7]:
totals_schema = StructType([ StructField("visits", StringType(), True),
                     StructField("hits", StringType(), True),
                     StructField("pageviews", StringType(), True),
                     StructField("bounces", StringType(), True),
                     StructField("transactionRevenue", StringType(), True),
                     StructField("newVisits", StringType(), True)
                        ])


trafficSource_schema = StructType(
  [
    StructField("campaign", StringType(), True),
    StructField("source", StringType(), True),
    StructField("medium", StringType(), True),
    StructField("keyword", StringType(), True),
    StructField("adContent", StringType(), True),
    StructField("adwordsClickInfo", StructType(
      [
        StructField('page', StringType() , True),
        StructField('slot', StringType() , True),
        StructField('criteriaParameters', StringType() , True),
        StructField('gclId', StringType() , True),
        StructField('adNetworkType', StringType() , True),
        StructField('isVideoAd', StringType() , True),
      ]
    ), True),
    StructField('isTrueDirect', StringType() , True)
  ]
)

In [8]:
# train2 = train.withColumn("_totals", from_json(train["totals"], totals_schema))
train = train.withColumn("_trafficSource", from_json(train["trafficSource"], trafficSource_schema)
).withColumn("_totals", from_json(train["totals"], totals_schema
)).withColumn("_device", from_json(train["device"], deviceSchema
)).withColumn("_geoNetwork", from_json(train["geoNetwork"], geoNetworkSchema
))
                        
display(train)                     

channelGrouping date device fullVisitorId geoNetwork sessionId socialEngagementType totals trafficSource visitId visitNumber visitStartTime _trafficSource _totals _device _geoNetwork Organic Search 20160902 {"browser": "Chrome", "browserVersion": "not available in demo dataset", "browserSize": "not available in demo dataset", "operatingSystem": "Windows", "operatingSystemVersion": "not available in demo dataset", "isMobile": false, "mobileDeviceBranding": "not available in demo dataset", "mobileDeviceModel": "not available in demo dataset", "mobileInputSelector": "not available in demo dataset", "mobileDeviceInfo": "not available in demo dataset", "mobileDeviceMarketingName": "not available in demo dataset", "flashVersion": "not available in demo dataset", "language": "not available in demo dataset", "screenColors": "not available in demo dataset", "screenResolution": "not available in demo dataset", "deviceCategory": "desktop"} 1131660440785968503 {"continent": "Asia", "subContinent": "Western Asia", "country": "Turkey", "region": "Izmir", "metro": "(not set)", "city": "Izmir", "cityId": "not available in demo dataset", "networkDomain": "ttnet.com.tr", "latitude": "not available in demo dataset", "longitude": "not available in demo dataset", "networkLocation": "not available in demo dataset"} 1131660440785968503_1472830385 Not Socially Engaged {"visits": "1", "hits": "1", "pageviews": "1", "bounces": "1", "newVisits": "1"} {"campaign": "(not set)", "source": "google", "medium": "organic", "keyword": "(not provided)", "adwordsClickInfo": {"criteriaParameters": "not available in demo dataset"}} 1472830385 1 1472830385 List((not set), google, organic, (not provided), null, List(null, null, not available in demo dataset, null, null, null), null) List(1, 1, 1, 1, null, 1) List(Chrome, not available in demo dataset, not available in demo dataset, Windows, not available in demo dataset, false, not available in demo dataset, not available in demo dataset, not available in demo dataset, not available in demo dataset, not available in demo dataset, not available in demo dataset, not available in demo dataset, not available in demo dataset, not available in demo dataset, desktop) List(Asia, Western Asia, Turkey, Izmir, (not set), Izmir, not available in demo dataset, ttnet.com.tr, not available in demo dataset, not available in demo dataset, not available in demo dataset) Organic Search 20160902 {"browser": "Firefox", "browserVersion": "not available in demo dataset", "browserSize": "not available in demo dataset", "operatingSystem": "Macintosh", "operatingSystemVersion": "not available in demo dataset", "isMobile": false, "mobileDeviceBranding": "not available in demo dataset", "mobileDeviceModel": "not available in demo dataset", "mobileInputSelector": "not available in demo dataset", "mobileDeviceInfo": "not available in demo dataset", "mobileDeviceMarketingName": "not available in demo dataset", "flashVersion": "not available in demo dataset", "language": "not available in demo dataset", "screenColors": "not available in demo dataset", "screenResolution": "not available in demo dataset", "deviceCategory": "desktop"} 377306020877927890 {"continent": "Oceania", "subContinent": "Australasia", "country": "Australia", "region": "not available in demo dataset", "metro": "not available in demo dataset", "city": "not available in demo dataset", "cityId": "not available in demo dataset", "networkDomain": "dodo.net.au", "latitude": "not available in demo dataset", "longitude": "not available in demo dataset", "networkLocation": "not available in demo dataset"} 377306020877927890_1472880147 Not Socially Engaged {"visits": "1", "hits": "1", "pageviews": "1", "bounces": "1", "newVisits": "1"} {"campaign": "(not set)", "source": "google", "medium": "organic", "keyword": "(not provided)", "adwordsClickInfo": {"criteriaParameters": "not available in demo dataset"}} 1472880147 1 1472880147 List((not set), google, organic, (not provided), null, List(

In [9]:
train_exploded = train.select('fullVisitorId','channelGrouping', 
                         'date', 
                         col('_device.*'),
                         'fullVisitorId',
                         col('_geoNetwork.*'),
                         'sessionId',
                         'socialEngagementType',
                         col('_totals.*'),
                         col('_trafficSource.*'),
                         'visitId',
                         'visitNumber',
                         'visitStartTime'
                             ) 

display(train_exploded)

fullVisitorId channelGrouping date browser browserVersion browserSize operatingSystem operatingSystemVersion isMobile mobileDeviceBranding mobileDeviceModel mobileInputSelector mobileDeviceInfo mobileDeviceMarketingName flashVersion language screenColors screenResolution deviceCategory fullVisitorId continent subContinent country region metro city cityId networkDomain latitude longitude networkLocation sessionId socialEngagementType visits hits pageviews bounces transactionRevenue newVisits campaign source medium keyword adContent adwordsClickInfo isTrueDirect visitId visitNumber visitStartTime 1131660440785968503 Organic Search 20160902 Chrome not available in demo dataset not available in demo dataset Windows not available in demo dataset false not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset desktop 1131660440785968503 Asia Western Asia Turkey Izmir (not set) Izmir not available in demo dataset ttnet.com.tr not available in demo dataset not available in demo dataset not available in demo dataset 1131660440785968503_1472830385 Not Socially Engaged 1 1 1 1 null 1 (not set) google organic (not provided) null List(null, null, not available in demo dataset, null, null, null) null 1472830385 1 1472830385 377306020877927890 Organic Search 20160902 Firefox not available in demo dataset not available in demo dataset Macintosh not available in demo dataset false not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset desktop 377306020877927890 Oceania Australasia Australia not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset dodo.net.au not available in demo dataset not available in demo dataset not available in demo dataset 377306020877927890_1472880147 Not Socially Engaged 1 1 1 1 null 1 (not set) google organic (not provided) null List(null, null, not available in demo dataset, null, null, null) null 1472880147 1 1472880147 3895546263509774583 Organic Search 20160902 Chrome not available in demo dataset not available in demo dataset Windows not available in demo dataset false not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset desktop 3895546263509774583 Europe Southern Europe Spain Community of Madrid (not set) Madrid not available in demo dataset unknown.unknown not available in demo dataset not available in demo dataset not available in demo dataset 3895546263509774583_1472865386 Not Socially Engaged 1 1 1 1 null 1 (not set) google organic (not provided) null List(null, null, not available in demo dataset, null, null, null) null 1472865386 1 1472865386 4763447161404445595 Organic Search 20160902 UC Browser not available in demo dataset not available in demo dataset Linux not available in demo dataset false not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset desktop 4763447161404445595 Asia Southeast Asia Indonesia not available in demo dataset not available in demo dataset not available in demo dataset not available in demo dataset unknown.unknown not available in demo dataset not available in demo dataset not available in demo dataset 4763447161404445595_1472881213 Not Socially Engaged 1 1 1 1 null 1 (not s

In [10]:
print("# of row" , train_exploded.count())
print("# of cols" , len(train_exploded.columns))

# of row 903653
# of cols 49

In [11]:
selected_features = ['fullVisitorId','bounces', 'visits', 'newVisits', 'hits', 'pageviews' , 'visitNumber', 'transactionRevenue']

train_selected = train_exploded.select(selected_features)
  
#  'channelGrouping',
#  'date',
#  'fullVisitorId',
#  'sessionId',
#  'visitId',
#  'visitNumber',
#  'visitStartTime',
#  'browser',
#  'deviceCategory',
#  'isMobile',
#  'operatingSystem',
#  'city',
#  'continent',
#  'country',
#  'metro',
#  'networkDomain',
#  'region',
#  'subContinent',
#  'bounces',
#  'hits',
#  'visits',
#  'newVisits',
#  'pageviews',
#  'transactionRevenue',
#  'adContent',
#  'campaign',
#  'isTrueDirect',
#  'keyword',
#  'medium',
#  'source')

print("# of row" , train_selected.count())
print("# of cols" , len(train_selected.columns))

# of row 903653
# of cols 8

In [12]:
# train_fillna_revenue = train_selected.select("transactionRevenue").fillna(0.0)
# df.fillna( { 'a':0, 'b':0 } )

train_fillna = train_selected.fillna( { "transactionRevenue":0 , 
                             "visitNumber" : 0 , 
                             "bounces" : 0 , 
                             "visits" : 0 , 
                             "newVisits" : 0 , 
                             "hits" : 0 , 
                             "pageviews" : 0
                            } )

train_fillna.filter(col("transactionRevenue").isNull()).count()

Out[ 50 ]: 0

In [13]:
train_convert_to_double = train_fillna.withColumn("visitNumber_flt", col("visitNumber").cast("double")
).withColumn("bounces_flt", col("bounces").cast("double")
).withColumn("visits_flt", col("visits").cast("double")
).withColumn("newVisits_flt", col("newVisits").cast("double")
).withColumn("hits_flt", col("hits").cast("double")
).withColumn("pageviews_flt", col("pageviews").cast("double")
).withColumn("transactionRevenue_flt", col("transactionRevenue").cast("double"))

train_convert_to_double.printSchema()

root
-- fullVisitorId: string (nullable = true)
-- bounces: string (nullable = false)
-- visits: string (nullable = false)
-- newVisits: string (nullable = false)
-- hits: string (nullable = false)
-- pageviews: string (nullable = false)
-- visitNumber: string (nullable = false)
-- transactionRevenue: string (nullable = false)
-- visitNumber_flt: double (nullable = true)
-- bounces_flt: double (nullable = true)
-- visits_flt: double (nullable = true)
-- newVisits_flt: double (nullable = true)
-- hits_flt: double (nullable = true)
-- pageviews_flt: double (nullable = true)
-- transactionRevenue_flt: double (nullable = true)

In [14]:
train_groupby = train_convert_to_double.groupby('fullVisitorId').sum()

train_groupby_renamed = train_groupby.withColumnRenamed("sum(visitNumber_flt)", "visitNumber_flt"
).withColumnRenamed("sum(bounces_flt)", "bounces_flt"
).withColumnRenamed("sum(bounces_flt)", "bounces_flt"
).withColumnRenamed("sum(visits_flt)", "visits_flt"
).withColumnRenamed("sum(newVisits_flt)", "newVisits_flt"                   
).withColumnRenamed("sum(hits_flt)", "hits_flt"                      
).withColumnRenamed("sum(pageviews_flt)", "pageviews_flt"                     
).withColumnRenamed("sum(transactionRevenue_flt)", "transactionRevenue_flt")                       
                    
display(train_groupby_renamed)

fullVisitorId visitNumber_flt bounces_flt visits_flt newVisits_flt hits_flt pageviews_flt transactionRevenue_flt 6940815913920553634 1.0 1.0 1.0 1.0 1.0 1.0 0.0 9169995120881264768 6.0 2.0 3.0 1.0 4.0 4.0 0.0 7019324769188325239 6.0 1.0 3.0 1.0 9.0 9.0 0.0 4182863769903710608 1.0 1.0 1.0 1.0 1.0 1.0 0.0 5194629126653011632 1.0 1.0 1.0 1.0 1.0 1.0 0.0 3307158041295976924 55.0 9.0 10.0 1.0 18.0 17.0 0.0 3216697237390563528 1.0 1.0 1.0 1.0 1.0 1.0 0.0 3805485490023701730 1.0 1.0 1.0 1.0 1.0 1.0 0.0 3611676034400073896 3.0 0.0 2.0 1.0 9.0 8.0 0.0 1718327138234260099 1.0 1.0 1.0 1.0 1.0 1.0 0.0 7325732945180921463 1.0 1.0 1.0 1.0 1.0 1.0 0.0 9402561690303978508 1.0 1.0 1.0 1.0 1.0 1.0 0.0 8794784697796986323 1.0 1.0 1.0 1.0 1.0 1.0 0.0 8951275750194001824 1.0 1.0 1.0 1.0 1.0 1.0 0.0 8140763001419038455 1.0 0.0 1.0 1.0 5.0 4.0 0.0 3207138918374590777 1.0 0.0 1.0 1.0 3.0 3.0 0.0 1754393156351978145 3.0 0.0 2.0 1.0 22.0 18.0 0.0 5101634632725994589 1.0 0.0 1.0 1.0 15.0 11.0 0.0 7909278615042772348 1.0 0.0 1.0 1.0 20.0 15.0 0.0 3483576563116422100 1.0 1.0 1.0 1.0 1.0 1.0 0.0 5465718217914670249 1.0 1.0 1.0 1.0 1.0 1.0 0.0 8218879917790625885 1.0 1.0 1.0 1.0 1.0 1.0 0.0 8059198476985973362 6.0 3.0 3.0 1.0 3.0 3.0 0.0 7433400063601477724 3.0 1.0 2.0 1.0 3.0 3.0 0.0 5881894652289592998 1.0 1.0 1.0 1.0 1.0 1.0 0.0 6423020663200072834 1.0 1.0 1.0 1.0 1.0 1.0 0.0 4924331792706126960 10.0 1.0 4.0 1.0 10.0 10.0 0.0 1998368269427224170 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1785522620165932146 1.0 1.0 1.0 1.0 1.0 1.0 0.0 4210528328969956783 1.0 1.0 1.0 1.0 1.0 1.0 0.0 8223876734974006674 1.0 1.0 1.0 1.0 1.0 1.0 0.0 7475519838387835440 3.0 2.0 2.0 1.0 2.0 2.0 0.0 3169354673181960316 1.0 1.0 1.0 1.0 1.0 1.0 0.0 4019994394699090762 1.0 1.0 1.0 1.0 1.0 1.0 0.0 6539044778325025330 1.0 1.0 1.0 1.0 1.0 1.0 0.0 892928671823362189 1.0 1.0 1.0 1.0 1.0 1.0 0.0 3339834971259422630 28.0 5.0 7.0 1.0 31.0 28.0 0.0 2711256867656868720 6.0 2.0 3.0 1.0 4.0 4.0 0.0 8843161209704563602 1.0 0.0 1.0 1.0 2.0 2.0 0.0 6799978125910208903 1.0 0.0 1.0 1.0 3.0 3.0 0.0 9829206894823510789 10.0 2.0 4.0 1.0 9.0 9.0 0.0 6232771690607504721 3.0 1.0 2.0 1.0 11.0 7.0 0.0 8523109535078910684 36.0 6.0 8.0 1.0 10.0 10.0 0.0 9820742635124113350 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1375654677340633658 6.0 0.0 3.0 1.0 44.0 36.0 0.0 2410900639753013179 1.0 1.0 1.0 1.0 1.0 1.0 0.0 5696606283088904888 3.0 2.0 2.0 1.0 2.0 2.0 0.0 8787860603214245091 28.0 4.0 7.0 1.0 24.0 21.0 0.0 5369322403284617066 1.0 1.0 1.0 1.0 1.0 1.0 0.0 5517185695876877980 1.0 0.0 1.0 1.0 4.0 4.0 0.0 5783527265241201136 1.0 0.0 1.0 1.0 10.0 7.0 0.0 7240516757795848110 3.0 1.0 2.0 1.0 22.0 12.0 0.0 3226090614182295559 1.0 0.0 1.0 1.0 27.0 19.0 0.0 1364621692287873533 1.0 1.0 1.0 1.0 1.0 1.0 0.0 971484420624519212 1.0 1.0 1.0 1.0 1.0 1.0 0.0 245694258566188982 6.0 3.0 3.0 1.0 3.0 3.0 0.0 1971903860805797159 10.0 4.0 4.0 1.0 4.0 4.0 0.0 1413343623066126746 1.0 1.0 1.0 1.0 1.0 1.0 0.0 2271206593656851292 1.0 1.0 1.0 1.0 1.0 1.0 0.0 0332027557866490026 21.0 2.0 6.0 1.0 56.0 44.0 0.0 999151229155004780 1.0 0.0 1.0 1.0 11.0 7.0 0.0 7857609472007443501 1.0 1.0 1.0 1.0 1.0 1.0 0.0 4789067326331386645 10.0 4.0 4.0 1.0 4.0 4.0 0.0 2412636316977012005 1.0 0.0 1.0 1.0 9.0 8.0 0.0 1819777116499947647 1.0 0.0 1.0 1.0 10.0 9.0 0.0 5577289515884641375 6.0 1.0 3.0 1.0 29.0 21.0 0.0 8137651767049257105 3.0 1.0 2.0 1.0 16.0 14.0 0.0 4927414362714506526 3.0 2.0 2.0 1.0 2.0 2.0 0.0 8204355114423835280 1.0 1.0 1.0 1.0 1.0 1.0 0.0 3944775101021890608 1.0 1.0 1.0 1.0 1.0 1.0 0.0 675929736373298003 1.0 1.0 1.0 1.0 1.0 1.0 0.0 904524693379393643 1.0 0.0 1.0 1.0 3.0 3.0 0.0 6292881197236568266 3.0 1.0 2.0 1.0 8.0 6.0 0.0 5053334124541235269 1.0 0.0 1.0 1.0 10.0 8.0 0.0 5208942793129243636 9.0 3.0 5.0 2.0 8.0 8.0 0.0 6601013215546260569 3.0 2.0 2.0 1.0 2.0 2.0 0.0 681506993669643404 1.0 1.0 1.0 1.0 1.0 1.0 0.0 134926360025904300 1.0 1.0 1.0 1.0 1.0 1.0 0.0 4921209176560944416 1.0 1.0 1.0 1.0 1.0 1.0 0.0 5844325870511040345 1.0 0.0 1.0 1.0 5.0 5.0 0.0 863766298135

In [15]:
# categorical_feature_encoded = ['channelGroupingIndex', 'browserIndex', 'deviceCategoryIndex', 'isMobileIndex' , 'countryIndex' , 'mediumIndex', 'sourceIndex']
# categorical_feature_encoded = ['channelGrouping', 'browser', 'deviceCategory', 'isMobile' , 'country' , 'medium', 'source']

numerical_features = ['bounces_flt', 'visits_flt', 'newVisits_flt', 'hits_flt', 'pageviews_flt' , 'visitNumber_flt']

# feature_columns = categorical_feature_encoded + numerical_features 
feature_columns = numerical_features

label_column = ['transactionRevenue_flt']


In [16]:
train_ = train_groupby_renamed.select(feature_columns + label_column)
display(train_)

bounces_flt visits_flt newVisits_flt hits_flt pageviews_flt visitNumber_flt transactionRevenue_flt 1.0 1.0 1.0 1.0 1.0 1.0 0.0 2.0 3.0 1.0 4.0 4.0 6.0 0.0 1.0 3.0 1.0 9.0 9.0 6.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 9.0 10.0 1.0 18.0 17.0 55.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 0.0 2.0 1.0 9.0 8.0 3.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 0.0 1.0 1.0 5.0 4.0 1.0 0.0 0.0 1.0 1.0 3.0 3.0 1.0 0.0 0.0 2.0 1.0 22.0 18.0 3.0 0.0 0.0 1.0 1.0 15.0 11.0 1.0 0.0 0.0 1.0 1.0 20.0 15.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 3.0 3.0 1.0 3.0 3.0 6.0 0.0 1.0 2.0 1.0 3.0 3.0 3.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 4.0 1.0 10.0 10.0 10.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 2.0 2.0 1.0 2.0 2.0 3.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 5.0 7.0 1.0 31.0 28.0 28.0 0.0 2.0 3.0 1.0 4.0 4.0 6.0 0.0 0.0 1.0 1.0 2.0 2.0 1.0 0.0 0.0 1.0 1.0 3.0 3.0 1.0 0.0 2.0 4.0 1.0 9.0 9.0 10.0 0.0 1.0 2.0 1.0 11.0 7.0 3.0 0.0 6.0 8.0 1.0 10.0 10.0 36.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 0.0 3.0 1.0 44.0 36.0 6.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 2.0 2.0 1.0 2.0 2.0 3.0 0.0 4.0 7.0 1.0 24.0 21.0 28.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 0.0 1.0 1.0 4.0 4.0 1.0 0.0 0.0 1.0 1.0 10.0 7.0 1.0 0.0 1.0 2.0 1.0 22.0 12.0 3.0 0.0 0.0 1.0 1.0 27.0 19.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 3.0 3.0 1.0 3.0 3.0 6.0 0.0 4.0 4.0 1.0 4.0 4.0 10.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 2.0 6.0 1.0 56.0 44.0 21.0 0.0 0.0 1.0 1.0 11.0 7.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 4.0 4.0 1.0 4.0 4.0 10.0 0.0 0.0 1.0 1.0 9.0 8.0 1.0 0.0 0.0 1.0 1.0 10.0 9.0 1.0 0.0 1.0 3.0 1.0 29.0 21.0 6.0 0.0 1.0 2.0 1.0 16.0 14.0 3.0 0.0 2.0 2.0 1.0 2.0 2.0 3.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 0.0 1.0 1.0 3.0 3.0 1.0 0.0 1.0 2.0 1.0 8.0 6.0 3.0 0.0 0.0 1.0 1.0 10.0 8.0 1.0 0.0 3.0 5.0 2.0 8.0 8.0 9.0 0.0 2.0 2.0 1.0 2.0 2.0 3.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 0.0 1.0 1.0 5.0 5.0 1.0 0.0 0.0 1.0 1.0 3.0 3.0 1.0 0.0 0.0 2.0 1.0 12.0 12.0 6.0 0.0 0.0 1.0 1.0 5.0 4.0 1.0 0.0 0.0 3.0 1.0 17.0 17.0 6.0 6.795E7 1.0 1.0 1.0 1.0 1.0 1.0 0.0 0.0 1.0 1.0 2.0 2.0 1.0 0.0 0.0 1.0 1.0 3.0 3.0 1.0 0.0 0.0 1.0 1.0 2.0 2.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 2.0 1.0 9.0 9.0 3.0 0.0 2.0 3.0 1.0 8.0 8.0 6.0 0.0 2.0 4.0 1.0 6.0 6.0 10.0 0.0 0.0 1.0 1.0 2.0 2.0 1.0 0.0 1.0 3.0 1.0 11.0 10.0 6.0 0.0 0.0 1.0 1.0 3.0 2.0 1.0 0.0 0.0 1.0 1.0 5.0 5.0 1.0 0.0 0.0 1.0 1.0 8.0 7.0 1.0 0.0 2.0 4.0 1.0 14.0 12.0 10.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 2.0 2.0 1.0 2.0 2.0 3.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 0.0 1.0 1.0 2.0 2.0 1.0 0.0 0.0 1.0 1.0 2.0 2.0 1.0 0.0 0.0 1.0 1.0 10.0 9.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 0.0 1.0 1.0 2.0 2.0 1.0 0.0 1.0 4.0 1.0 48.0 46.0 10.0 3.7975E8 0.0 1.0 1.0 46.0 21.0 1.0 0.0 0.0 1.0 1.0 7.0 6.0 1.0 0.0 0.0 2.0 0.0 32.0 27.0 7.0 0.0 2.0 2.0 1.0 2.0 2.0 3.0 0.0 2.0 2.0 1.0 2.0 2.0 3.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 2.0 1.0 1.0 0.0 0.0 1.0 1.0 2.0 2.0 1.0 0.0 0.0 1.0 1.0 2.0 2.0 1.0 0.0 1.0 2.0 1.0 7.0 7.0 3.0 0.0 0.0 1.0 1.0 2.0 2.0 1.0 0.0 0.0 1.0 1.0 2.0 2.0 1.0 0.0 0.0 1.0 1.0 2.0 2.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.0 0.0 1.0 1.0 2.0 2.0 1.0 0.0 0.0 1.0 1.0 4.0 3.0 1.0 0.0 0.0 1.0 1.0 4.0 4.0 1.0 0.0 1.0 2.0 1.0 13.0 9.0 3.0 0.0 0.0 1.0 1.0 15.0 13.0 

In [17]:
describe_train_df = train_.describe()

display(describe_train_df)

summary bounces_flt visits_flt newVisits_flt hits_flt pageviews_flt visitNumber_flt transactionRevenue_flt count 714167 714167 714167 714167 714167 714167 714167 mean 0.630986870017797 1.26532449693139 0.9844476151936452 5.816111637754195 4.870661904008446 2.8658297008962887 2156458.139342759 stddev 0.9297667589287714 1.430618059751293 0.13915030985765672 18.41700775080243 14.128870279787064 127.25578806674645 1.0838832927307674E8 min 0.0 1.0 0.0 1.0 0.0 1.0 0.0 max 186.0 278.0 3.0 4995.0 4160.0 63315.0 7.711343E10

# Normalizing features 
  - x = value 
  - dl = min of attribute 
  - dh = max of attribute 
  - nl = min of expected range 
  - nh = max of expected range

In [19]:
# call function
#normalize columns
def normalizing_column(c , dL, dH):
  nL = 0
  nH = 1
  numi = (float(c) - dL) * (nH-nL)
  denom = dH - dL
  div = float(numi) / float(denom)
  normalized = float(div + nL)
  return normalized

normalizing_column_udf = udf(normalizing_column, DoubleType())


# names = train_.schema.names
names = ['hits_flt',
 'pageviews_flt',
 'visitNumber_flt',
 'bounces_flt',
 'visits_flt',
 'newVisits_flt',
        ]
for colname in names:
  dL = float(describe_train_df.collect()[3][colname])
  dH = float(describe_train_df.collect()[4][colname])
  train_ = train_.withColumn('normalized_' + str(colname), 
                           normalizing_column_udf(colname, lit(dL) , lit(dH))
                          )    

In [20]:
display(train_.describe())

summary bounces_flt visits_flt newVisits_flt hits_flt pageviews_flt visitNumber_flt transactionRevenue_flt normalized_hits_flt normalized_pageviews_flt normalized_visitNumber_flt normalized_bounces_flt normalized_visits_flt normalized_newVisits_flt count 714167 714167 714167 714167 714167 714167 714167 714167 714167 714167 714167 714167 714167 mean 0.630986870017797 1.26532449693139 0.9844476151936452 5.816111637754195 4.870661904008446 2.8658297008962887 2156458.139342759 9.643795830505168E-4 0.0011708321884636224 2.9469464903438255E-5 0.003392402526977573 9.57850169427408E-4 0.32814920506455214 stddev 0.9297667589287706 1.430618059751293 0.13915030985765672 18.417007750802437 14.12887027978706 127.25578806674658 1.0838832927307698E8 0.0036878269424914763 0.0033963630480257382 0.002009915469986835 0.00499874601574608 0.005164686136286253 0.046383436619218905 min 0.0 1.0 0.0 1.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 max 186.0 278.0 3.0 4995.0 4160.0 63315.0 7.711343E10 1.0 1.0 1.0 1.0 1.0 1.0

In [21]:
selected_train_ = train_.select('transactionRevenue_flt', 'normalized_hits_flt', 'normalized_pageviews_flt', 'normalized_visitNumber_flt', 'normalized_bounces_flt', 'normalized_visits_flt', 'normalized_newVisits_flt')
display(selected_train_)

transactionRevenue_flt normalized_hits_flt normalized_pageviews_flt normalized_visitNumber_flt normalized_bounces_flt normalized_visits_flt normalized_newVisits_flt 0.0 4.0048057669203043E-4 7.211538461538462E-4 0.0 0.0 0.0 0.3333333333333333 0.0 4.0048057669203043E-4 4.807692307692308E-4 0.0 0.0 0.0 0.3333333333333333 0.0 0.01261513816579896 0.0125 1.4214865590548694E-4 0.005376344086021506 0.010830324909747292 0.3333333333333333 0.0 0.002603123748498198 0.0033653846153846156 0.0 0.0 0.0 0.3333333333333333 0.0 0.010212254705646776 0.009375 0.0 0.0 0.0 0.3333333333333333 0.0 0.0 2.403846153846154E-4 0.0 0.005376344086021506 0.0 0.3333333333333333 0.0 0.001001201441730076 0.001201923076923077 0.0 0.0 0.0 0.3333333333333333 0.0 0.0012014417300760913 0.0016826923076923078 0.0 0.0 0.0 0.3333333333333333 0.0 0.002803364036844213 0.003125 3.158859020121932E-5 0.0 0.0036101083032490976 0.3333333333333333 0.0 4.0048057669203043E-4 7.211538461538462E-4 0.0 0.0 0.0 0.3333333333333333 0.0 0.001001201441730076 0.001201923076923077 3.158859020121932E-5 0.005376344086021506 0.0036101083032490976 0.3333333333333333 0.0 0.0 2.403846153846154E-4 0.0 0.005376344086021506 0.0 0.3333333333333333 0.0 0.0 2.403846153846154E-4 0.0 0.005376344086021506 0.0 0.3333333333333333 0.0 2.0024028834601522E-4 4.807692307692308E-4 3.158859020121932E-5 0.010752688172043012 0.0036101083032490976 0.3333333333333333 0.0 0.0 2.403846153846154E-4 0.0 0.005376344086021506 0.0 0.3333333333333333 0.0 0.0 2.403846153846154E-4 0.0 0.005376344086021506 0.0 0.3333333333333333 0.0 0.0 2.403846153846154E-4 0.0 0.005376344086021506 0.0 0.3333333333333333 0.0 0.0 2.403846153846154E-4 0.0 0.005376344086021506 0.0 0.3333333333333333 0.0 0.001001201441730076 0.0014423076923076924 7.89714755030483E-5 0.005376344086021506 0.007220216606498195 0.3333333333333333 0.0 2.0024028834601522E-4 4.807692307692308E-4 0.0 0.0 0.0 0.3333333333333333 0.0 2.0024028834601522E-4 4.807692307692308E-4 0.0 0.0 0.0 0.3333333333333333 0.0 2.0024028834601522E-4 4.807692307692308E-4 0.0 0.0 0.0 0.3333333333333333 0.0 2.0024028834601522E-4 4.807692307692308E-4 0.0 0.0 0.0 0.3333333333333333 0.0 4.0048057669203043E-4 4.807692307692308E-4 0.0 0.0 0.0 0.3333333333333333 0.0 2.0024028834601522E-4 4.807692307692308E-4 0.0 0.0 0.0 0.3333333333333333 0.0 4.0048057669203043E-4 7.211538461538462E-4 0.0 0.0 0.0 0.3333333333333333 0.0 0.0 2.403846153846154E-4 0.0 0.005376344086021506 0.0 0.3333333333333333 0.0 0.0 2.403846153846154E-4 0.0 0.005376344086021506 0.0 0.3333333333333333 0.0 0.0 2.403846153846154E-4 0.0 0.005376344086021506 0.0 0.3333333333333333 0.0 2.0024028834601522E-4 4.807692307692308E-4 0.0 0.0 0.0 0.3333333333333333 0.0 2.0024028834601522E-4 4.807692307692308E-4 0.0 0.0 0.0 0.3333333333333333 0.0 0.0 2.403846153846154E-4 0.0 0.005376344086021506 0.0 0.3333333333333333 0.0 0.0 2.403846153846154E-4 0.0 0.005376344086021506 0.0 0.3333333333333333 0.0 0.0 2.403846153846154E-4 0.0 0.005376344086021506 0.0 0.3333333333333333 0.0 0.002002402883460152 0.0026442307692307694 2.2112013140853523E-4 0.010752688172043012 0.01444043321299639 0.3333333333333333 0.0 2.0024028834601522E-4 4.807692307692308E-4 0.0 0.0 0.0 0.3333333333333333 0.0 4.0048057669203043E-4 7.211538461538462E-4 0.0 0.0 0.0 0.3333333333333333 0.0 0.006007208650380457 0.0057692307692307696 3.158859020121932E-5 0.0 0.0036101083032490976 0.3333333333333333 0.0 0.002002402883460152 0.0026442307692307694 4.738288530182898E-5 0.0 0.0036101083032490976 0.3333333333333333 0.0 0.0 2.403846153846154E-4 0.0 0.005376344086021506 0.0 0.3333333333333333 0.0 0.0 2.403846153846154E-4 0.0 0.005376344086021506 0.0 0.3333333333333333 0.0 0.0 2.403846153846154E-4 0.0 0.005376344086021506 0.0 0.3333333333333333 0.0 0.0 2.403846153846154E-4 0.0 0.005376344086021506 0.0 0.3333333333333333 0.0 0.0 2.403846153846154E-4 0.0 0.005376344086021506 0.0 0.3333333333333333 0.0 0.0016019223067681217 0.0021634615384615386 1.4214865590548694E-4 0.010752688172043012 0.010830324

In [22]:
train_pd = selected_train_.toPandas()

In [23]:
train_pd.dtypes

Out[ 60 ]: 
transactionRevenue_flt float64
normalized_hits_flt float64
normalized_pageviews_flt float64
normalized_visitNumber_flt float64
normalized_bounces_flt float64
normalized_visits_flt float64
normalized_newVisits_flt float64
dtype: object

In [24]:
train_x = train_pd.drop(['transactionRevenue_flt'], axis = 1)
n_cols = train_x.shape[1]
train_x.head()

Out[ 61 ]: 
 normalized_hits_flt normalized_pageviews_flt normalized_visitNumber_flt \
0 0.000601 0.000962 0.000000 
1 0.004005 0.003606 0.000000 
2 0.004205 0.003846 0.000000 
3 0.003204 0.004087 0.002132 
4 0.000200 0.000481 0.000032 

 normalized_bounces_flt normalized_visits_flt normalized_newVisits_flt 
0 0.000000 0.000000 0.333333 
1 0.000000 0.000000 0.333333 
2 0.000000 0.000000 0.333333 
3 0.080645 0.054152 0.333333 
4 0.010753 0.003610 0.333333

In [25]:
train_y2 = train_pd.transactionRevenue_flt
train_y2.head()

Out[ 62 ]: 
0 0.0
1 0.0
2 0.0
3 0.0
4 0.0
Name: transactionRevenue_flt, dtype: float64

In [26]:
train_y2_log = np.log(train_y2)
train_y2_log.head()

Out[ 63 ]: 
0 -inf
1 -inf
2 -inf
3 -inf
4 -inf
Name: transactionRevenue_flt, dtype: float64

In [27]:
train_y2 = train_y2_log.replace('-inf', 0.0)
train_y2.describe()
# train_y2.describe()

Out[ 65 ]: 
count 714167.000000
mean 0.249542
std 2.099521
min 0.000000
25% 0.000000
50% 0.000000
75% 0.000000
max 25.068543
Name: transactionRevenue_flt, dtype: float64

In [29]:
# define
model = Sequential()

#add model layers
model.add(Dense(7, activation='relu', input_shape=(n_cols,)))
model.add(Dense(7, activation='relu'))
model.add(Dense(1))

model.compile(loss='mean_squared_error', optimizer='adam')

#7 input model - mse ---- loss = 5.9617 , after new log --> loss =  3.1654

In [30]:
# from keras.callbacks import EarlyStopping
#set early stopping monitor so the model stops training when it won't improve anymore
# early_stopping_monitor = EarlyStopping(patience=3)
#train model
model.fit(train_x, train_y2, epochs=10)

Epoch 1/10

 32/714167 [..............................] - ETA: 1:30:35 - loss: 2.9792e-06
 1504/714167 [..............................] - ETA: 2:19 - loss: 5.2760 
 3040/714167 [..............................] - ETA: 1:20 - loss: 5.1833
 4544/714167 [..............................] - ETA: 1:01 - loss: 5.0636
 6080/714167 [..............................] - ETA: 51s - loss: 5.1586 
 7584/714167 [..............................] - ETA: 46s - loss: 4.8007
 9152/714167 [..............................] - ETA: 42s - loss: 4.7604
 10656/714167 [..............................] - ETA: 39s - loss: 4.8978
 12160/714167 [..............................] - ETA: 37s - loss: 4.7919
 13696/714167 [..............................] - ETA: 35s - loss: 4.8887
 15200/714167 [..............................] - ETA: 34s - loss: 4.8801
 16672/714167 [..............................] - ETA: 33s - loss: 4.9560
 18176/714167 [..............................] - ETA: 32s - loss: 4.8657
 19712/714167 [..............................] - ETA: 31s - loss: 4.8805
 21216/714167 [..............................] - ETA: 31s - loss: 4.7445
 22752/714167 [..............................] - ETA: 30s - loss: 4.7988
 24256/714167 [>.............................] - ETA: 29s - loss: 4.7060
 25792/714167 [>.............................] - ETA: 29s - loss: 4.6829
 27264/714167 [>.............................] - ETA: 29s - loss: 4.6996
 28768/714167 [>.............................] - ETA: 28s - loss: 4.7236
 30272/714167 [>.............................] - ETA: 28s - loss: 4.7407
 31776/714167 [>.............................] - ETA: 28s - loss: 4.7076
 33312/714167 [>.............................] - ETA: 27s - loss: 4.6728
 34816/714167 [>.............................] - ETA: 27s - loss: 4.6612
 36320/714167 [>.............................] - ETA: 27s - loss: 4.6700
 37824/714167 [>.............................] - ETA: 26s - loss: 4.6997
 39328/714167 [>.............................] - ETA: 26s - loss: 4.6491
 40864/714167 [>.............................] - ETA: 26s - loss: 4.6173
 42368/714167 [>.............................] - ETA: 26s - loss: 4.5940
 43904/714167 [>.............................] - ETA: 26s - loss: 4.6345
 45408/714167 [>.............................] - ETA: 25s - loss: 4.6245
 46912/714167 [>.............................] - ETA: 25s - loss: 4.6100
 48416/714167 [=>............................] - ETA: 25s - loss: 4.6008
 49920/714167 [=>............................] - ETA: 25s - loss: 4.5727
 51328/714167 [=>............................] - ETA: 25s - loss: 4.5407
 52832/714167 [=>............................] - ETA: 25s - loss: 4.5588
 54336/714167 [=>............................] - ETA: 25s - loss: 4.5374
 55840/714167 [=>............................] - ETA: 24s - loss: 4.5675
 57024/714167 [=>............................] - ETA: 24s - loss: 4.5391
 58560/714167 [=>............................] - ETA: 24s - loss: 4.5144
 60096/714167 [=>............................] - ETA: 24s - loss: 4.4825
 61536/714167 [=>............................] - ETA: 24s - loss: 4.4438
 63040/714167 [=>............................] - ETA: 24s - loss: 4.4285
 64544/714167 [=>............................] - ETA: 24s - loss: 4.4085
 66048/714167 [=>............................] - ETA: 24s - loss: 4.3903
 67584/714167 [=>............................] - ETA: 24s - loss: 4.3925
 69120/714167 [=>............................] - ETA: 23s - loss: 4.4195
 70624/714167 [=>............................] - ETA: 23s - loss: 4.4328
 72160/714167 [==>...........................] - ETA: 23s - loss: 4.4443
 73696/714167 [==>...........................] - ETA: 23s - loss: 4.4266
 75232/714167 [==>...........................] - ETA: 23s - loss: 4.4336
 76704/714167 [==>...........................] - ETA: 23s - loss: 4.4317
 78240/714167 [==>...........................] - ETA: 23s - loss: 4.4283
 79744/714167 [==>...........................] - ETA: 23s - loss: 4.4262
 81248/714167 [==>........................

In [31]:
# define
model2 = Sequential()

#add model layers
model2.add(Dense(200, activation='relu', input_shape=(n_cols,)))
model2.add(Dense(200, activation='relu'))
model2.add(Dense(200, activation='relu'))
model2.add(Dense(1))

model2.compile(loss='mean_squared_error', optimizer='adam')
model2.fit(train_x, train_y2, epochs=10)

#200 input model - mse ---- loss = 6.1056 , after new log --> loss = 3.1392

Epoch 1/10

 32/714167 [..............................] - ETA: 1:43:01 - loss: 9.9266e-04
 960/714167 [..............................] - ETA: 4:03 - loss: 4.0189 
 1888/714167 [..............................] - ETA: 2:22 - loss: 3.7965
 2784/714167 [..............................] - ETA: 1:49 - loss: 4.4476
 3648/714167 [..............................] - ETA: 1:33 - loss: 4.2049
 4544/714167 [..............................] - ETA: 1:23 - loss: 3.9857
 5408/714167 [..............................] - ETA: 1:16 - loss: 3.9163
 6336/714167 [..............................] - ETA: 1:10 - loss: 4.1602
 7264/714167 [..............................] - ETA: 1:06 - loss: 4.1754
 8224/714167 [..............................] - ETA: 1:03 - loss: 4.1680
 9184/714167 [..............................] - ETA: 1:00 - loss: 4.3621
 10080/714167 [..............................] - ETA: 58s - loss: 4.2830 
 11040/714167 [..............................] - ETA: 56s - loss: 4.3344
 12000/714167 [..............................] - ETA: 54s - loss: 4.2148
 12960/714167 [..............................] - ETA: 53s - loss: 4.1544
 13920/714167 [..............................] - ETA: 52s - loss: 4.0683
 14880/714167 [..............................] - ETA: 51s - loss: 4.1814
 15808/714167 [..............................] - ETA: 50s - loss: 4.1926
 16768/714167 [..............................] - ETA: 49s - loss: 4.1268
 17728/714167 [..............................] - ETA: 48s - loss: 4.1361
 18656/714167 [..............................] - ETA: 48s - loss: 4.1145
 19616/714167 [..............................] - ETA: 47s - loss: 4.0914
 20576/714167 [..............................] - ETA: 47s - loss: 4.0865
 21536/714167 [..............................] - ETA: 46s - loss: 4.0561
 22464/714167 [..............................] - ETA: 46s - loss: 4.0535
 23424/714167 [..............................] - ETA: 45s - loss: 3.9867
 24384/714167 [>.............................] - ETA: 45s - loss: 3.9171
 25344/714167 [>.............................] - ETA: 44s - loss: 3.8791
 26304/714167 [>.............................] - ETA: 44s - loss: 3.8277
 27264/714167 [>.............................] - ETA: 44s - loss: 3.8384
 28192/714167 [>.............................] - ETA: 43s - loss: 3.8263
 29152/714167 [>.............................] - ETA: 43s - loss: 3.8708
 30112/714167 [>.............................] - ETA: 43s - loss: 3.8425
 31072/714167 [>.............................] - ETA: 43s - loss: 3.8015
 32032/714167 [>.............................] - ETA: 42s - loss: 3.7670
 32992/714167 [>.............................] - ETA: 42s - loss: 3.7312
 33952/714167 [>.............................] - ETA: 42s - loss: 3.7129
 34912/714167 [>.............................] - ETA: 42s - loss: 3.6769
 35872/714167 [>.............................] - ETA: 41s - loss: 3.7141
 36832/714167 [>.............................] - ETA: 41s - loss: 3.7320
 37792/714167 [>.............................] - ETA: 41s - loss: 3.6883
 38752/714167 [>.............................] - ETA: 41s - loss: 3.6824
 39712/714167 [>.............................] - ETA: 41s - loss: 3.6875
 40640/714167 [>.............................] - ETA: 40s - loss: 3.7006
 41600/714167 [>.............................] - ETA: 40s - loss: 3.7068
 42560/714167 [>.............................] - ETA: 40s - loss: 3.7131
 43520/714167 [>.............................] - ETA: 40s - loss: 3.6710
 44448/714167 [>.............................] - ETA: 40s - loss: 3.6651
 45344/714167 [>.............................] - ETA: 40s - loss: 3.6448
 46240/714167 [>.............................] - ETA: 40s - loss: 3.6337
 47072/714167 [>.............................] - ETA: 40s - loss: 3.5856
 47936/714167 [=>............................] - ETA: 39s - loss: 3.6014
 48896/714167 [=>............................] - ETA: 39s - loss: 3.5813
 49856/714167 [=>............................] - ETA: 39s - loss: 3.6007
 50816/714167 [=>.......................

In [32]:
# define
model3 = Sequential()

#add model layers
model3.add(Dense(7, activation='relu', input_shape=(n_cols,)))
model3.add(Dense(7, activation='relu'))
model3.add(Dense(1))



#create a custome loss and compile model using mse as a measure of model performance
from keras import backend as K
def root_mean_squared_error(y_true, y_pred):
        return K.sqrt(K.mean(K.square(y_pred - y_true), axis=-1)) 

model3.compile(optimizer = "adam", loss = root_mean_squared_error)


from keras.callbacks import EarlyStopping
#set early stopping monitor so the model stops training when it won't improve anymore
# early_stopping_monitor = EarlyStopping(patience=3)
#train model
model3.fit(train_x, train_y2, epochs=5)

#loss: 0.2492

Epoch 1/5

 32/714167 [..............................] - ETA: 1:36:49 - loss: 0.0752
 1440/714167 [..............................] - ETA: 2:33 - loss: 0.3000 
 2944/714167 [..............................] - ETA: 1:27 - loss: 0.2800
 4448/714167 [..............................] - ETA: 1:05 - loss: 0.2726
 5952/714167 [..............................] - ETA: 54s - loss: 0.2668 
 7488/714167 [..............................] - ETA: 48s - loss: 0.2641
 8960/714167 [..............................] - ETA: 44s - loss: 0.2642
 10432/714167 [..............................] - ETA: 41s - loss: 0.2693
 11904/714167 [..............................] - ETA: 39s - loss: 0.2753
 13376/714167 [..............................] - ETA: 37s - loss: 0.2717
 14880/714167 [..............................] - ETA: 35s - loss: 0.2749
 16384/714167 [..............................] - ETA: 34s - loss: 0.2660
 17888/714167 [..............................] - ETA: 33s - loss: 0.2658
 19360/714167 [..............................] - ETA: 32s - loss: 0.2632
 20896/714167 [..............................] - ETA: 32s - loss: 0.2617
 22400/714167 [..............................] - ETA: 31s - loss: 0.2593
 23904/714167 [>.............................] - ETA: 30s - loss: 0.2603
 25408/714167 [>.............................] - ETA: 30s - loss: 0.2627
 26912/714167 [>.............................] - ETA: 29s - loss: 0.2648
 28416/714167 [>.............................] - ETA: 29s - loss: 0.2595
 29920/714167 [>.............................] - ETA: 29s - loss: 0.2590
 31424/714167 [>.............................] - ETA: 28s - loss: 0.2639
 32928/714167 [>.............................] - ETA: 28s - loss: 0.2658
 34464/714167 [>.............................] - ETA: 28s - loss: 0.2662
 35968/714167 [>.............................] - ETA: 27s - loss: 0.2651
 37472/714167 [>.............................] - ETA: 27s - loss: 0.2631
 38976/714167 [>.............................] - ETA: 27s - loss: 0.2631
 40320/714167 [>.............................] - ETA: 27s - loss: 0.2677
 41792/714167 [>.............................] - ETA: 26s - loss: 0.2642
 43232/714167 [>.............................] - ETA: 26s - loss: 0.2629
 44736/714167 [>.............................] - ETA: 26s - loss: 0.2627
 46240/714167 [>.............................] - ETA: 26s - loss: 0.2616
 47744/714167 [=>............................] - ETA: 26s - loss: 0.2635
 49248/714167 [=>............................] - ETA: 26s - loss: 0.2635
 50752/714167 [=>............................] - ETA: 25s - loss: 0.2639
 52256/714167 [=>............................] - ETA: 25s - loss: 0.2632
 53728/714167 [=>............................] - ETA: 25s - loss: 0.2611
 55200/714167 [=>............................] - ETA: 25s - loss: 0.2619
 56672/714167 [=>............................] - ETA: 25s - loss: 0.2638
 58144/714167 [=>............................] - ETA: 25s - loss: 0.2637
 59584/714167 [=>............................] - ETA: 25s - loss: 0.2625
 60960/714167 [=>............................] - ETA: 24s - loss: 0.2612
 62464/714167 [=>............................] - ETA: 24s - loss: 0.2621
 63968/714167 [=>............................] - ETA: 24s - loss: 0.2607
 65472/714167 [=>............................] - ETA: 24s - loss: 0.2602
 66976/714167 [=>............................] - ETA: 24s - loss: 0.2594
 68448/714167 [=>............................] - ETA: 24s - loss: 0.2584
 69920/714167 [=>............................] - ETA: 24s - loss: 0.2602
 71424/714167 [==>...........................] - ETA: 24s - loss: 0.2591
 72928/714167 [==>...........................] - ETA: 24s - loss: 0.2611
 74432/714167 [==>...........................] - ETA: 23s - loss: 0.2610
 75936/714167 [==>...........................] - ETA: 23s - loss: 0.2597
 77440/714167 [==>...........................] - ETA: 23s - loss: 0.2579
 78944/714167 [==>...........................] - ETA: 23s - loss: 0.2590
 80448/714167 [==>...........................] 